### AITech — Uczenie maszynowe — laboratoria
# 11. Sieci neuronowe (Keras)

Keras to napisany w języku Python interfejs do platformy TensorFlow, służącej do uczenia maszynowego.

Aby z niego korzystać, trzeba zainstalować bibliotekę TensorFlow:
 * `pip`: https://www.tensorflow.org/install
 * `conda`: https://docs.anaconda.com/anaconda/user-guide/tasks/tensorflow

Przykład implementacji sieci neuronowej do rozpoznawania cyfr ze zbioru MNIST, według https://keras.io/examples/vision/mnist_convnet

In [1]:
# Konieczne importy

import numpy as np
from tensorflow import keras
from tensorflow.keras import layers

2023-05-25 10:52:05.523296: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-05-25 10:52:06.689624: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-05-25 10:52:06.689658: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2023-05-25 10:52:09.444585: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-

In [2]:
# Przygotowanie danych

num_classes = 10  # liczba klas
input_shape = (784,)  # wymiary wejścia

# podział danych na zbiory uczący i testowy
(x_train, y_train), (x_test, y_test) = keras.datasets.mnist.load_data()

# skalowanie pikseli do przedziału [0, 1]
x_train = x_train.astype("float32") / 255
x_test = x_test.astype("float32") / 255
# spłaszczenie dwuwymiarowych obrazów do jednowymiarowych wektorów
x_train = x_train.reshape(60000, 784)  # 784 = 28 * 28
x_test = x_test.reshape(10000, 784)
print("x_train shape:", x_train.shape)
print(x_train.shape[0], "train samples")
print(x_test.shape[0], "test samples")

# konwersja danych kategorycznych na binarne
y_train = keras.utils.to_categorical(y_train, num_classes)
y_test = keras.utils.to_categorical(y_test, num_classes)

x_train shape: (60000, 784)
60000 train samples
10000 test samples


In [3]:
# Stworzenie modelu

model = keras.Sequential(
    [
        keras.Input(shape=input_shape),  # warstwa wejściowa
        layers.Dense(512, activation="relu", input_shape=(784,)),  # warstwa ukryta 1
        layers.Dense(256, activation="relu"),  # warstwa ukryta 2
        layers.Dense(num_classes, activation="softmax"),  # warstwa wyjściowa
    ]
)

model.summary()  # wyświetlmy podsumowanie modelu

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 512)               401920    
                                                                 
 dense_1 (Dense)             (None, 256)               131328    
                                                                 
 dense_2 (Dense)             (None, 10)                2570      
                                                                 
Total params: 535,818
Trainable params: 535,818
Non-trainable params: 0
_________________________________________________________________


2023-05-25 10:52:13.751127: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2023-05-25 10:52:13.752395: W tensorflow/compiler/xla/stream_executor/cuda/cuda_driver.cc:265] failed call to cuInit: UNKNOWN ERROR (303)
2023-05-25 10:52:13.752552: I tensorflow/compiler/xla/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (ELLIOT): /proc/driver/nvidia/version does not exist
2023-05-25 10:52:13.755949: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [4]:
# Kompilacja modelu
model.compile(
    loss="categorical_crossentropy",  # standardowa funkcja kosztu dla kalsyfikacji wieloklasowej
    optimizer="adam",  # optymalizator
    metrics=["accuracy"],  # lista metryk
)

# Uczenie modelu
model.fit(
    x_train,
    y_train,
    batch_size=128,  # wielkość wsadu (paczki)
    epochs=10,  # liczba epok
    validation_split=0.1,  # wielkość zbioru walidacyjnego
)

Epoch 1/10
422/422 [==============================] - 9s 18ms/step - loss: 0.2402 - accuracy: 0.9290 - val_loss: 0.1133 - val_accuracy: 0.9652
Epoch 2/10
422/422 [==============================] - 7s 16ms/step - loss: 0.0878 - accuracy: 0.9728 - val_loss: 0.0776 - val_accuracy: 0.9763
Epoch 3/10
422/422 [==============================] - 7s 18ms/step - loss: 0.0552 - accuracy: 0.9829 - val_loss: 0.0688 - val_accuracy: 0.9792
Epoch 4/10
422/422 [==============================] - 7s 16ms/step - loss: 0.0381 - accuracy: 0.9881 - val_loss: 0.0632 - val_accuracy: 0.9823
Epoch 5/10
422/422 [==============================] - 7s 17ms/step - loss: 0.0286 - accuracy: 0.9908 - val_loss: 0.0782 - val_accuracy: 0.9788
Epoch 6/10
422/422 [==============================] - 7s 17ms/step - loss: 0.0227 - accuracy: 0.9926 - val_loss: 0.0733 - val_accuracy: 0.9807
Epoch 7/10
422/422 [==============================] - 7s 17ms/step - loss: 0.0167 - accuracy: 0.9944 - val_loss: 0.0824 - val_accuracy: 0.9798

In [5]:
# Ewaluacja modelu
score = model.evaluate(x_test, y_test, verbose=0)
print("Test loss:", score[0])
print("Test accuracy:", score[1])

Test loss: 0.10677255690097809
Test accuracy: 0.9757000207901001
